# 用户登录网站配合数据库练习题

练习1. 回顾不用数据库实现用户登录系统

请测试下面的程序，注意：

1. 先在该ipynb文件所在目录下创建`data`文件夹
2. 创建两个账户，登录后并进入输入内容界面，输入数据，保存后，查看是否在`data`文件夹下有新内容产生。

In [ ]:
from http.server import HTTPServer, SimpleHTTPRequestHandler
from urllib.parse import parse_qs 
import os

PORT = 8020

class CustomHandler(SimpleHTTPRequestHandler):
    def do_GET(self):
        # 处理 /data/<username>/user-input.html 动态页面
        if self.path.startswith("/data/") and self.path.endswith("/user-input.html"):
            parts = self.path.split("/")
            if len(parts) >= 4:
                username = parts[2]  # /data/username/user-input.html → parts[2] = username
                self.send_response(200)
                self.send_header("Content-type", "text/html; charset=utf-8")
                self.end_headers()
                html_content = f'''
<!DOCTYPE html>
<html lang="zh-CN">
<head>
    <meta charset="UTF-8">
    <title>用户输入</title>
</head>
<body>
    <h2>当前用户: {username}</h2>
    <form action="/save" method="post">
        <label for="user-input">请输入内容:</label><br>
        <input type="text" id="user-input" name="user-input" required><br><br>
        <input type="hidden" name="username" value="{username}">
        <button type="submit">保存</button>
    </form>
</body>
</html>
                '''
                self.wfile.write(html_content.encode("utf-8"))
            else:
                self.send_response(400)
                self.end_headers()
                self.wfile.write(b"Invalid path")
        elif self.path.endswith(".html"):
            # 原有逻辑：处理 login.html, register.html 等静态页面
            try:
                filename = self.path[1:]  # Remove leading '/'
                with open(filename, "r", encoding="utf-8") as f:
                    content = f.read()
                self.send_response(200)
                self.send_header("Content-type", "text/html; charset=utf-8")
                self.end_headers()
                self.wfile.write(content.encode("utf-8"))
            except FileNotFoundError:
                self.send_response(404)
                self.send_header("Content-type", "text/html; charset=utf-8")
                self.end_headers()
                self.wfile.write(b"404 Not Found")
        else:
            self.send_response(404)
            self.send_header("Content-type", "text/html; charset=utf-8")
            self.end_headers()
            self.wfile.write(b"404 Not Found")
    def do_POST(self):  
        # 处理注册表单提交  
        if self.path == "/register":  
            content_length = int(self.headers["Content-Length"])  
            post_data = self.rfile.read(content_length).decode("utf-8")  
            form_data = parse_qs(post_data)  

            username = form_data.get("username", [""])[0]  
            password = form_data.get("password", [""])[0]  

            # 检查用户名是否已存在

            with open("???", "r") as f:  # TODO 用户名到哪个文件里查找？
                users = f.readlines()  
            existing_usernames = [line.strip().split(",")[0] for line in users]


            if username in existing_usernames:
                self.send_response(400)  
                self.send_header("Content-type", "text/html; charset=utf-8")  
                self.end_headers()  
                self.wfile.write("<h1>用户名已存在！</h1><a href='/register.html'>返回注册页面</a>".encode("utf-8"))
                return

            # 简单存储到文件（实际项目应使用数据库）  
            with open("users.txt", "a") as f:  
                f.write(f"{username},{password}\n")  
            # 返回成功响应  
            self.send_response(200)  
            self.send_header("Content-type", "text/html; charset=utf-8")  
            self.end_headers()  
            self.wfile.write("<h1>注册成功！</h1><a href='/login.html'>登录</a>".encode("utf-8"))
        elif self.path == "/login": 
            content_length = int(self.headers["Content-Length"])  
            post_data = self.rfile.read(content_length).decode("utf-8")  
            form_data = parse_qs(post_data)  
  
            username = form_data.get("username", [""])[0]  
            password = form_data.get("password", [""])[0]  
  
            # 验证用户  
            with open("users.txt", "r") as f:  
                users = f.readlines()  
  
            user_found = any(line.strip() == f"{username},{password}" for line in users)  
  
            if user_found:  
                # 创建用户数据目录（如果不存在）
                user_dir = os.path.join("data", username)
                os.makedirs(user_dir, exist_ok=True)

                self.send_response(200)  
                self.send_header("Content-type", "text/html; charset=utf-8")  
                self.end_headers()  
                redirect_url = f"/data/{username}/user-input.html"
                self.wfile.write(f"<h1>登录成功！</h1><a href='{redirect_url}'>进入用户页面</a>".encode("utf-8"))  
            else:  
                self.send_response(401)  
                self.send_header("Content-type", "text/html; charset=utf-8")  
                self.end_headers()  
                self.wfile.write("<h1>登录失败，用户名或密码错误！</h1><a href='/login.html'>返回</a>".encode("utf-8"))
        elif self.path == "/save":
            content_length = int(self.headers["Content-Length"])
            post_data = self.rfile.read(content_length).decode("utf-8")
            form_data = parse_qs(post_data)

            username = form_data.get("username", [""])[0]
            user_input = form_data.get("user-input", [""])[0]

            user_dir = os.path.join("data", username)

            # 保存内容到 last_content.txt
            content_file = os.path.join(user_dir, "last_content.txt")
            with open(content_file, "w", encoding="utf-8") as f:
                f.write(user_input)

            self.send_response(200)
            self.send_header("Content-type", "text/html; charset=utf-8")
            self.end_headers()
            self.wfile.write(f"<h1>保存成功！</h1><a href='/data/{username}/user-input.html'>返回</a>".encode("utf-8"))

with HTTPServer(("127.0.0.1", PORT), CustomHandler) as httpd:
    print(f"服务器运行中，访问 http://localhost:{PORT}")
    httpd.serve_forever()

练习2. 回顾数据库的基本操作

In [ ]:
import sqlite3

conn = sqlite3.connect("user.db")
cursor = conn.cursor()
cursor.execute("""
    CREATE TABLE IF NOT EXISTS users (
        username TEXT PRIMARY KEY,
        password TEXT NOT NULL
    )
""")

user = "user1"
passw = "111"
cursor.execute("INSERT into users (username, password) values (?, ?)", (???, ???))  # TODO, 两个问号对应的变量
conn.commit()
cursor.close()
conn.close()

练习3. 将用户名和密码存储到数据库里


In [ ]:
from http.server import HTTPServer, SimpleHTTPRequestHandler
from urllib.parse import parse_qs 
import os
import sqlite3

PORT = 8020

# 初始化数据库
def init_db():
    conn = sqlite3.connect("user.db")
    cursor = conn.cursor()
    cursor.execute("""
        CREATE TABLE IF NOT EXISTS users (
            username TEXT PRIMARY KEY,
            password TEXT NOT NULL
        )
    """)
    conn.commit()
    cursor.close()
    conn.???  # TODO, 完成后，先关掉数据库

class CustomHandler(SimpleHTTPRequestHandler):
    def do_GET(self):
        # 处理 /data/<username>/user-input.html 动态页面
        if self.path.startswith("/data/") and self.path.endswith("/user-input.html"):
            parts = self.path.split("/")
            if len(parts) >= 4:
                username = parts[2]  # /data/username/user-input.html → parts[2] = username
                self.send_response(200)
                self.send_header("Content-type", "text/html; charset=utf-8")
                self.end_headers()
                html_content = f'''
<!DOCTYPE html>
<html lang="zh-CN">
<head>
    <meta charset="UTF-8">
    <title>用户输入</title>
</head>
<body>
    <h2>当前用户: {username}</h2>
    <form action="/save" method="post">
        <label for="user-input">请输入内容:</label><br>
        <input type="text" id="user-input" name="user-input" required><br><br>
        <input type="hidden" name="username" value="{username}">
        <button type="submit">保存</button>
    </form>
</body>
</html>
                '''
                self.wfile.write(html_content.encode("utf-8"))
            else:
                self.send_response(400)
                self.end_headers()
                self.wfile.write(b"Invalid path")
        elif self.path.endswith(".html"):
            # 原有逻辑：处理 login.html, register.html 等静态页面
            try:
                filename = self.path[1:]  # Remove leading '/'
                with open(filename, "r", encoding="utf-8") as f:
                    content = f.read()
                self.send_response(200)
                self.send_header("Content-type", "text/html; charset=utf-8")
                self.end_headers()
                self.wfile.write(content.encode("utf-8"))
            except FileNotFoundError:
                self.send_response(404)
                self.send_header("Content-type", "text/html; charset=utf-8")
                self.end_headers()
                self.wfile.write(b"404 Not Found")
        else:
            self.send_response(404)
            self.send_header("Content-type", "text/html; charset=utf-8")
            self.end_headers()
            self.wfile.write(b"404 Not Found")
    
    def do_POST(self):  
        # 处理注册表单提交  
        if self.path == "/register":  
            content_length = int(self.headers["Content-Length"])  
            post_data = self.rfile.read(content_length).decode("utf-8")  
            form_data = parse_qs(post_data)  

            username = form_data.get("username", [""])[0]  
            password = form_data.get("password", [""])[0]  

            # 检查用户名是否已存在
            conn = sqlite3.connect("???")   # TODO, 去哪个文件里检查用户名是否存在？
            cursor = conn.cursor()
            cursor.execute("??? username FROM users WHERE username = ?", (username,))  # TODO，用哪种方法（关键词）来查询数据库里的内容?
            existing = cursor.fetchone()
            if existing:
                cursor.close()
                conn.close()
                self.send_response(400)  
                self.send_header("Content-type", "text/html; charset=utf-8")  
                self.end_headers()  
                self.wfile.write("<h1>用户名已存在！</h1><a href='/register.html'>返回注册页面</a>".encode("utf-8"))
                return

            # 存储到数据库
            cursor.execute("INSERT INTO users (username, password) VALUES (?, ?)", (???, ???))  # TODO， 用户名和密码分别存储在哪个变量里？
            conn.commit()
            cursor.close()
            conn.close()

            # 返回成功响应  
            self.send_response(200)  
            self.send_header("Content-type", "text/html; charset=utf-8")  
            self.end_headers()  
            self.wfile.write("<h1>注册成功！</h1><a href='/login.html'>登录</a>".encode("utf-8"))

        elif self.path == "/login": 
            content_length = int(self.headers["Content-Length"])  
            post_data = self.rfile.read(content_length).decode("utf-8")  
            form_data = parse_qs(post_data)  
  
            username = form_data.get("username", [""])[0]  
            password = form_data.get("password", [""])[0]  
  
            # 验证用户  
            conn = sqlite3.connect("user.db")
            cursor = conn.cursor()
            cursor.execute("SELECT password ??? users WHERE username = ?", (username,))  # TODO， select关键词来对表里内容进行查询时，配合哪个词？
            row = cursor.fetchone()
            cursor.close()
            conn.close()

            if row and row[0] == password:  
                # 创建用户数据目录（如果不存在）
                user_dir = os.path.join("data", username)
                os.makedirs(user_dir, exist_ok=True)

                self.send_response(200)  
                self.send_header("Content-type", "text/html; charset=utf-8")  
                self.end_headers()  
                redirect_url = f"/data/{username}/user-input.html"
                self.wfile.write(f"<h1>登录成功！</h1><a href='{redirect_url}'>进入用户页面</a>".encode("utf-8"))  
            else:  
                self.send_response(401)  
                self.send_header("Content-type", "text/html; charset=utf-8")  
                self.end_headers()  
                self.wfile.write("<h1>登录失败，用户名或密码错误！</h1><a href='/login.html'>返回</a>".encode("utf-8"))

        elif self.path == "/save":
            content_length = int(self.headers["Content-Length"])
            post_data = self.rfile.read(content_length).decode("utf-8")
            form_data = parse_qs(post_data)

            username = form_data.get("username", [""])[0]
            user_input = form_data.get("user-input", [""])[0]

            user_dir = os.path.join("data", username)

            # 保存内容到 last_content.txt
            content_file = os.path.join(user_dir, "last_content.txt")
            with open(content_file, "w", encoding="utf-8") as f:
                f.write(user_input)

            self.send_response(200)
            self.send_header("Content-type", "text/html; charset=utf-8")
            self.end_headers()
            self.wfile.write(f"<h1>保存成功！</h1><a href='/data/{username}/user-input.html'>返回</a>".encode("utf-8"))

# 初始化数据库
init_db()

with HTTPServer(("127.0.0.1", PORT), CustomHandler) as httpd:
    print(f"服务器运行中，访问 http://localhost:{PORT}")
    httpd.serve_forever()